In [90]:
import pandas as pd
import os
import numpy as np
from sklearn.model_selection import train_test_split  
import warnings
import xgboost as xgb
from xgboost import XGBRanker
import time
import datetime
warnings.filterwarnings('ignore')

In [2]:
# specifying some paths
path = r"C:\Users\janse\OneDrive\Bureaublad\Master\Data Mining Techniques\Repo\Assignment2\data"
testpath = os.path.join(path, 'test_set_VU_DM.csv')
trainpath = os.path.join(path, 'training_set_VU_DM.csv')
samplepath = os.path.join(path, 'train_sample.csv')
resultpath = os.path.join(path, 'result.csv')


In [3]:
# load train_main
# made a function for quick reusability during development
def reload_train():
    train_main = pd.read_csv(trainpath)
    train_main.date_time = pd.to_datetime(train_main.date_time)
    return train_main

In [4]:
train_main = reload_train()

# Feature extraction functions

In [83]:
def average_prop_score(train_df):
    cols = ['prop_id', 'price_usd', 'prop_starrating', 'prop_review_score', 'prop_brand_bool', 'prop_location_score1', 'prop_location_score2']
    df = train_df[cols]
    df['prop_location_score2'] = df['prop_location_score2'].fillna(df.prop_location_score2.mean())
    return df.groupby('prop_id').agg('mean').reset_index()

def rate(row, mean_rate):
    if row['srch_id'] < 20:
        return mean_rate
    else:
        return row['click_bool']
    
def avg_click_rate(train_main):
    prop_click_rate = train_main[['prop_id','click_bool', 'srch_id']].groupby('prop_id').agg({'click_bool' : 'mean', 'srch_id': 'count'}).reset_index()
    mean_rate = prop_click_rate.click_bool.mean()
    prop_click_rate['click_rate'] = prop_click_rate.apply(lambda x: rate(x, mean_rate), axis=1)
    return prop_click_rate[['prop_id', 'click_rate']]

def split_sets(df, test_size = 0.2, shuffle=False, downsample=False):
    '''
        Returns: X_train, X_test, Y_train, Y_test
    '''
    df_train, df_test = train_test_split(df.sort_values('srch_id'), test_size=test_size, shuffle=shuffle) 
    
    if downsample:
        df_train = downsample(df_train)
    
    X_train = df_train.drop(['click_bool','booking_bool'] , axis=1)
    X_train = X_train.fillna(X_train.mean())
    X_test = df_test.drop(['click_bool','booking_bool'] , axis=1)    
    X_test = X_test.fillna(X_test.mean())
    
    Y_train = df_train.click_bool + df_train.booking_bool * 4
    Y_test = df_test.click_bool + df_train.booking_bool * 4
    
    target_train = df_train.click_bool + 4 * df_train.booking_bool
    target_test = df_test.click_bool + 4 * df_test.booking_bool    
    
    return X_train, X_test, Y_train, Y_test, target_train, target_test

def cumulate_comp_scores(train_df):    
    # Cumulative competitor scores

    cols = [col for col in train_df.columns if col.endswith('rate_percent_diff')]
    cols2 = [col for col in train_df.columns if col.endswith('_rate')]
    cols3 = [col for col in train_df.columns if col.endswith('_inv')]

    df = train_df[cols.extend(cols2).extend(cols3).extend(['prop_id'])]
    df['comp_rate_percent_diff_cumm'] = 0

    for col1, col2, col3 in zip(cols, cols2, cols3):
        df['comp_rate_percent_diff_cumm'] += df[col1].fillna(0) * df[col2].fillna(0) * (1 - df[col3].fillna(0))
        
    df = train2.drop(cols, axis=1)
    df = train2.drop(cols2, axis=1)
    df = train2.drop(cols3, axis=1)
    return df

def avg_prop_features(train_main, test_main = None, predict_phase=False):
    cols = [
       'visitor_hist_starrating', 'visitor_hist_adr_usd', 'prop_id', 'prop_starrating', 'prop_review_score', 'prop_brand_bool',
       'prop_location_score1', 'prop_location_score2',
       'prop_log_historical_price', 'price_usd', 'promotion_flag',
       'srch_length_of_stay', 'srch_booking_window',
       'srch_adults_count', 'srch_children_count', 'srch_room_count',
       'srch_saturday_night_bool', 'srch_query_affinity_score',
       'orig_destination_distance', 'random_bool']
    df = train_main[cols].groupby('prop_id').agg(['mean', 'std']) # median?
    
    if predict_phase:
        df = df.merge(test_main[cols + ['srch_id']], on='prop_id')
    else:
        df = df.merge(train_main[cols + ['srch_id']], on='prop_id')   
        
    return df


# Models

In [84]:
from sklearn.neighbors import KNeighborsClassifier

def train_gxboost_ranker(train, lr = 0.1, n_estimators=200, max_depth=6, objective='rank:ndcg'):
    train = train.sort_values('srch_id')
    train['label'] = train.click_bool + 4 * train.booking_bool
    group_train = train[['srch_id','prop_id']].groupby('srch_id').agg('count').prop_id.values
    
    X = train.drop(['srch_id', 'prop_id', 'label', 'date_time', 'click_bool', 'booking_bool'], axis=1).values    
    Y = train.label.values
    
    model = XGBRanker(n_estimators=n_estimators, 
                      learning_rate=lr,  
                      max_depth=max_depth, 
                      objective=objective,
                      sub_sample = 1,
                      colsample_bytree = 0.8,
                      verbosity = 2#,
#                       predictor='gpu_predictor'
                     )
    model.fit(X, Y, group_train, verbose=2)
    
    return model

def train_KNN(X_train, Y_train):
    X = X_train.drop(['srch_id','prop_id'], axis=1).values
    Y = Y_train.values
    return KNeighborsClassifier(n_neighbors=20).fit(X, Y)


# Evaluation functions

In [85]:
def evaluate(X_test, pred, target_test):
    prop_srch = X_test[['srch_id', 'prop_id']]
    prop_srch['value'] = pred
    prop_srch['actual'] = target_test.values
    eval_ndcg(prop_srch.sort_values(['srch_id', 'value'], ascending=False), 'srch_id', 'value','actual', n=5000)
    return prop_srch

def dcg_at_k(r, k):
    r = np.asfarray(r)[:k]
    if r.size:
        return np.sum(np.subtract(np.power(2, r), 1) / np.log2(np.arange(2, r.size + 2)))
    return 0.


def ndcg_at_k(r, k):
    idcg = dcg_at_k(sorted(r, reverse=True), k)
    if not idcg:
        return 0.
    return dcg_at_k(r, k) / idcg

def eval_ndcg(df, srch_id_col, predict_col, value_col, n=9999999999999999):
    df = df.sort_values([srch_id_col, predict_col], ascending=False)
    k = 5
    ndcgs = []
    for i, srchid in enumerate(df[srch_id_col].unique()):
        if i == n:
            break
        if i % 10000 == 0 and i != 0:
            print(i)
            print(np.mean(ndcgs))
        r = df[df[srch_id_col] == srchid][value_col]
        ndcgs.append(ndcg_at_k(r,k))

    print(np.mean(ndcgs))


# Functions used to combine the above

In [86]:
def feature_eng(train_main):

    df = train_main[['prop_id', 'srch_id','date_time', 'click_bool', 'booking_bool']]        
    df = df.merge(avg_prop_features(train_main), on=['prop_id', 'srch_id'])    
    df = df.fillna(df.mean())
    return df.sort_values(['prop_id', 'srch_id'], ascending=[True, False])

def test_eng(test_main, train_main):
    df = avg_prop_features(train_main, test_main=test_main, predict_phase=True)  
    df = df.fillna(df.mean())
    return df.sort_values(['srch_id', 'prop_id'], ascending=[True, False])

def train_and_test(train, test, n_estimators=20, evaluate=True):    
    
    model = train_gxboost_ranker(train, n_estimators=n_estimators)
    
    if evaluate:
        test = test.sort_values('srch_id')
        for i, srch in enumerate(test.srch_id.unique()):
            X_t = test[test.srch_id == srch].drop(['srch_id', 'prop_id', 'date_time', 'click_bool', 'booking_bool'], axis=1).values
            pred = model.predict(X_t)
            if i == 0:
                predictions = pred
            else:
                predictions = np.append(predictions, pred)

        test['label'] = test.click_bool + 4 * test.booking_bool
        target_test = test.label
        results = evaluate(test, predictions, target_test)
    else:
        results = None
    return results, model

def predict(df_train, df_predict, model):
    test = test_eng(df_predict, df_train).fillna(0)
    
    for i, srch in enumerate(test.srch_id.unique()):
        df = test[test.srch_id == srch]
        X_t = df.drop(['srch_id', 'prop_id'], axis=1).values
        pred = model.predict(X_t)
        
        if i == 0:
            prop_srch = df[['srch_id', 'prop_id']]
            predictions = pred
        else:
            prop_srch = pd.concat([prop_srch, df[['srch_id', 'prop_id']]])
            predictions = np.append(predictions, pred)
            
    prop_srch['value'] = predictions      
    return prop_srch
        

# rankLib formatting

In [87]:
# Ranklib formatting
def f(x, label_col, query_col, feature_columns, cols2id):
    if x.name in feature_columns:
        return cols2id[x.name] + ':' + x.astype(str)
    elif x.name == query_col:
        return 'qid:' + x.astype(str)
    else:
        return x


def to_ranklib(df, label_col, query_col, target_file):
    cols = df.columns
    new_col_names = [col[0] + '_' + col[1] if (type(col) == tuple) else col for col in cols ]
    df.columns = new_col_names
    
    feature_columns = list(df.drop([label_col, query_col], axis=1).columns)
    cols2id = {col:str(i+1) for i,col in enumerate(feature_columns)}
    
    (df.apply(lambda x: f(x, label_col, query_col, feature_columns, cols2id))[[label_col, query_col] + feature_columns]
      .to_csv(target_file, sep=' ', index=False, header=None)
    )

# Main stuff

In [10]:
# Create main dataset
df = feature_eng2(train_main)
df_train = df[df.date_time < '2013-05-30']
df_test = df[df.date_time >= '2013-05-30']

In [91]:
# Start training / testing function with 1/x fraction of the data
start = time.time()

print(datetime.datetime.now(), ': Training')
results, model = train_and_test(pd.concat([df_train, df_test]), None, n_estimators=1000, evaluate=False)
print(datetime.datetime.now(), ': Done')

print(datetime.datetime.now(), ': Loading prediction data')
predict_data = pd.read_csv(testpath)
print(datetime.datetime.now(), ': Done')

print(datetime.datetime.now(), ': Generating predictions')
predictions = predict(train_main, predict_data, model)
print(datetime.datetime.now(), ': Done')

print(datetime.datetime.now(), ': Exporting to result.csv')
predictions = predictions.sort_values(['srch_id', 'value'], ascending=[True, False])
predictions.to_csv(os.path.join(path, 'result_with value.csv'))
predictions.to_csv(resultpath, index=False)[['srch_id', 'prop_id']]
print(datetime.datetime.now(), ': Done')
print('Time required: ', int(time.time()-start), 's')

2019-05-21 18:02:47.498501 : Start training
Training Done
2019-05-21 22:18:57.577818 : Finished training
2019-05-21 22:18:57.578816 : Loading prediction data
2019-05-21 22:19:24.488300 : Loaded data
2019-05-21 22:19:24.488300 : Generating predictions
2019-05-22 03:37:20.289334 : Done
2019-05-22 03:37:20.292327 : Exporting to result.csv
2019-05-22 03:37:35.747951 : Done
Time required:  34488 s


In [95]:

predictions2 = predictions
max_i = len(predictions.srch_id.unique())
for i, srch in enumerate(predictions.srch_id.unique()):
    if i == 0:
        result = predictions2[predictions2.srch_id == srch].iloc[::-1]
    else:
        result = pd.concat([result, predictions2[predictions2.srch_id == srch].iloc[::-1]])
    if i % int(max_i / 100):
        print(i / max_i)


5.017385239856101e-06
1.0034770479712202e-05
1.5052155719568304e-05
2.0069540959424405e-05
2.5086926199280506e-05
3.0104311439136607e-05
3.512169667899271e-05
4.013908191884881e-05
4.5156467158704914e-05
5.017385239856101e-05
5.519123763841712e-05
6.0208622878273215e-05
6.522600811812931e-05
7.024339335798542e-05
7.526077859784152e-05
8.027816383769762e-05
8.529554907755372e-05
9.031293431740983e-05
9.533031955726593e-05
0.00010034770479712202
0.00010536509003697814
0.00011038247527683423
0.00011539986051669033
0.00012041724575654643
0.00012543463099640254
0.00013045201623625863
0.00013546940147611474
0.00014048678671597085
0.00014550417195582693
0.00015052155719568304
0.00015553894243553915
0.00016055632767539524
0.00016557371291525135
0.00017059109815510743
0.00017560848339496355
0.00018062586863481966
0.00018564325387467574
0.00019066063911453185
0.00019567802435438796
0.00020069540959424405
0.00020571279483410016
0.00021073018007395627
0.00021574756531381236
0.00022076495055366847


0.0018965716206656063
0.0019015890059054625
0.0019066063911453185
0.0019116237763851746
0.0019166411616250308
0.0019216585468648868
0.0019266759321047429
0.0019316933173445991
0.0019367107025844551
0.0019417280878243112
0.0019467454730641674
0.0019517628583040235
0.0019567802435438795
0.0019617976287837355
0.0019668150140235915
0.001971832399263448
0.001976849784503304
0.00198186716974316
0.001986884554983016
0.001991901940222872
0.001996919325462728
0.0020019367107025846
0.0020069540959424407
0.0020119714811822967
0.0020169888664221527
0.0020220062516620087
0.0020270236369018648
0.0020320410221417212
0.0020370584073815773
0.0020420757926214333
0.0020470931778612893
0.0020521105631011454
0.0020571279483410014
0.002062145333580858
0.002067162718820714
0.00207218010406057
0.002077197489300426
0.002082214874540282
0.002087232259780138
0.0020922496450199945
0.0020972670302598505
0.0021022844154997065
0.0021073018007395626
0.0021123191859794186
0.0021173365712192746
0.002122353956459131
0.0

0.0038734214051689103
0.0038784387904087663
0.0038834561756486224
0.0038884735608884784
0.003893490946128335
0.003898508331368191
0.003903525716608047
0.003908543101847903
0.003913560487087759
0.003918577872327615
0.003923595257567471
0.003928612642807327
0.003933630028047183
0.00393864741328704
0.003943664798526896
0.003948682183766752
0.003953699569006608
0.003958716954246464
0.00396373433948632
0.003968751724726176
0.003973769109966032
0.003978786495205888
0.003983803880445744
0.0039888212656856
0.003993838650925456
0.003998856036165313
0.004003873421405169
0.004008890806645025
0.004013908191884881
0.004018925577124737
0.004023942962364593
0.004028960347604449
0.004033977732844305
0.0040389951180841615
0.0040440125033240175
0.0040490298885638735
0.0040540472738037295
0.0040590646590435864
0.0040640820442834425
0.0040690994295232985
0.0040741168147631545
0.0040791342000030106
0.004084151585242867
0.004089168970482723
0.004094186355722579
0.004099203740962435
0.004104221126202291
0.00

0.005915497197790344
0.0059205145830302
0.005925531968270056
0.005930549353509912
0.005935566738749768
0.005940584123989624
0.00594560150922948
0.005950618894469337
0.005955636279709193
0.005960653664949049
0.005965671050188905
0.005970688435428761
0.005975705820668617
0.005980723205908473
0.005985740591148329
0.005990757976388185
0.005995775361628041
0.006000792746867897
0.006005810132107753
0.006010827517347609
0.006015844902587466
0.006020862287827322
0.006025879673067178
0.006030897058307034
0.00603591444354689
0.006040931828786746
0.006045949214026602
0.006050966599266458
0.006055983984506314
0.00606100136974617
0.006066018754986026
0.006071036140225882
0.006076053525465739
0.006081070910705595
0.006086088295945451
0.006091105681185307
0.006096123066425163
0.006101140451665019
0.006106157836904875
0.006111175222144731
0.006116192607384587
0.006121209992624443
0.0061262273778642995
0.0061312447631041555
0.006136262148344012
0.006141279533583868
0.0061462969188237244
0.0061513143040

0.007952555605171921
0.007957572990411776
0.007962590375651633
0.007967607760891489
0.007972625146131345
0.0079776425313712
0.007982659916611057
0.007987677301850913
0.00799269468709077
0.007997712072330626
0.008002729457570482
0.008007746842810338
0.008012764228050194
0.00801778161329005
0.008022798998529906
0.008027816383769763
0.008032833769009618
0.008037851154249475
0.00804286853948933
0.008047885924729187
0.008052903309969042
0.008057920695208899
0.008062938080448756
0.00806795546568861
0.008072972850928468
0.008077990236168323
0.00808300762140818
0.008088025006648035
0.008093042391887892
0.008098059777127747
0.008103077162367604
0.008108094547607459
0.008113111932847316
0.008118129318087173
0.008123146703327028
0.008128164088566885
0.00813318147380674
0.008138198859046597
0.008143216244286452
0.008148233629526309
0.008153251014766164
0.008158268400006021
0.008163285785245876
0.008168303170485733
0.008173320555725588
0.008178337940965445
0.008183355326205302
0.008188372711445157


...

0.990376655109956
0.9903816724951958
0.9903866898804357
0.9903917072656756
0.9903967246509154
0.9904017420361553
0.9904067594213951
0.990411776806635
0.9904167941918749
0.9904218115771147
0.9904268289623546
0.9904318463475944
0.9904368637328342
0.9904418811180741
0.990446898503314
0.9904519158885539
0.9904569332737937
0.9904619506590335
0.9904669680442734
0.9904719854295133
0.9904770028147531
0.990482020199993
0.9904870375852328
0.9904920549704727
0.9904970723557125
0.9905020897409524
0.9905071071261923
0.9905121245114321
0.990517141896672
0.9905221592819118
0.9905271766671517
0.9905321940523916
0.9905372114376314
0.9905422288228712
0.9905472462081111
0.9905522635933509
0.9905572809785909
0.9905622983638307
0.9905673157490705
0.9905723331343104
0.9905773505195502
0.9905823679047902
0.99058738529003
0.9905924026752698
0.9905974200605097
0.9906024374457495
0.9906074548309893
0.9906124722162293
0.9906174896014691
0.990622506986709
0.9906275243719488
0.9906325417571886
0.9906375591424286
0

0.9925592176892934
0.9925642350745333
0.9925692524597731
0.992574269845013
0.9925792872302528
0.9925843046154926
0.9925893220007326
0.9925943393859724
0.9925993567712122
0.9926043741564521
0.9926093915416919
0.9926144089269319
0.9926194263121717
0.9926244436974115
0.9926294610826514
0.9926344784678912
0.992639495853131
0.992644513238371
0.9926495306236108
0.9926545480088507
0.9926595653940905
0.9926645827793303
0.9926696001645703
0.9926746175498101
0.99267963493505
0.9926846523202898
0.9926896697055296
0.9926946870907695
0.9926997044760094
0.9927047218612493
0.9927097392464891
0.9927147566317289
0.9927197740169688
0.9927247914022087
0.9927298087874485
0.9927348261726884
0.9927398435579282
0.992744860943168
0.9927498783284079
0.9927548957136478
0.9927599130988877
0.9927649304841275
0.9927699478693673
0.9927749652546072
0.9927799826398471
0.992785000025087
0.9927900174103268
0.9927950347955666
0.9928000521808065
0.9928050695660463
0.9928100869512863
0.9928151043365261
0.9928201217217659


0.9947518150391105
0.9947568324243504
0.9947618498095903
0.9947668671948301
0.9947718845800699
0.9947769019653098
0.9947819193505496
0.9947869367357896
0.9947919541210294
0.9947969715062692
0.9948019888915091
0.9948070062767489
0.9948120236619888
0.9948170410472287
0.9948220584324685
0.9948270758177084
0.9948320932029482
0.994837110588188
0.994842127973428
0.9948471453586678
0.9948521627439076
0.9948571801291475
0.9948621975143873
0.9948672148996273
0.9948722322848671
0.9948772496701069
0.9948822670553468
0.9948872844405866
0.9948923018258264
0.9948973192110664
0.9949023365963062
0.9949073539815461
0.9949123713667859
0.9949173887520257
0.9949224061372657
0.9949274235225055
0.9949324409077454
0.9949374582929852
0.994942475678225
0.9949474930634649
0.9949525104487048
0.9949575278339446
0.9949625452191845
0.9949675626044243
0.9949725799896642
0.994977597374904
0.9949826147601439
0.9949876321453838
0.9949926495306236
0.9949976669158634
0.9950026843011033
0.9950077016863432
0.99501271907158

0.9969393950036878
0.9969444123889276
0.9969494297741675
0.9969544471594074
0.9969594645446472
0.9969644819298871
0.9969694993151269
0.9969745167003667
0.9969795340856066
0.9969845514708465
0.9969895688560864
0.9969945862413262
0.996999603626566
0.9970046210118059
0.9970096383970458
0.9970146557822857
0.9970196731675255
0.9970246905527653
0.9970297079380052
0.997034725323245
0.9970397427084849
0.9970447600937248
0.9970497774789646
0.9970547948642045
0.9970598122494443
0.9970648296346842
0.9970698470199241
0.9970748644051639
0.9970798817904037
0.9970848991756436
0.9970899165608834
0.9970949339461234
0.9970999513313632
0.997104968716603
0.9971099861018429
0.9971150034870827
0.9971200208723225
0.9971250382575625
0.9971300556428023
0.9971350730280422
0.997140090413282
0.9971451077985218
0.9971501251837618
0.9971551425690016
0.9971601599542415
0.9971651773394813
0.9971701947247211
0.997175212109961
0.9971802294952009
0.9971852468804407
0.9971902642656806
0.9971952816509204
0.997200299036160

0.9991219575830251
0.9991269749682651
0.9991319923535049
0.9991370097387448
0.9991420271239846
0.9991470445092244
0.9991520618944644
0.9991570792797042
0.999162096664944
0.9991671140501839
0.9991721314354237
0.9991771488206636
0.9991821662059035
0.9991871835911433
0.9991922009763832
0.999197218361623
0.9992022357468628
0.9992072531321028
0.9992122705173426
0.9992172879025825
0.9992223052878223
0.9992273226730621
0.999232340058302
0.9992373574435419
0.9992423748287818
0.9992473922140216
0.9992524095992614
0.9992574269845013
0.9992624443697411
0.999267461754981
0.9992724791402209
0.9992774965254607
0.9992825139107006
0.9992875312959404
0.9992925486811803
0.9992975660664202
0.99930258345166
0.9993076008368998
0.9993126182221397
0.9993176356073795
0.9993226529926195
0.9993276703778593
0.9993326877630991
0.999337705148339
0.9993427225335788
0.9993477399188188
0.9993527573040586
0.9993577746892984
0.9993627920745383
0.9993678094597781
0.9993728268450179
0.9993778442302579
0.9993828616154977


In [99]:
#result.to_csv(resultpath, index=False)
df.head()

prop_id  srch_id           date_time  click_bool  booking_bool  \
4772218        1   320180 2012-12-05 13:46:23           0             0   
4768857        1   319953 2013-02-25 08:56:48           0             0   
4681591        1   314064 2013-06-09 20:22:16           0             0   
4653476        1   312176 2013-03-19 18:02:59           0             0   
4618280        1   309861 2013-05-08 11:09:14           0             0   

         (visitor_hist_starrating, mean)  (visitor_hist_starrating, std)  \
4772218                         2.536667                        0.834406   
4768857                         2.536667                        0.834406   
4681591                         2.536667                        0.834406   
4653476                         2.536667                        0.834406   
4618280                         2.536667                        0.834406   

         (visitor_hist_adr_usd, mean)  (visitor_hist_adr_usd, std)  \
4772218                     99.346667                    41.556383   
4768857                     99.346667                    41.556383   
4681591                     99.346667                    41.556383   
4653476                     99.346667                    41.556383   
4618280                     99.346667                    41.556383   

         (prop_starrating, mean)     ...       promotion_flag  \
4772218                        2     ...                    0   
4768857                        2     ...                    0   
4681591                        2     ...                    0   
4653476                        2     ...                    0   
4618280                        2     ...                    0   

         srch_length_of_stay  srch_booking_window  srch_adults_count  \
4772218                    1                    2                  1   
4768857                    3                   35                  1   
4681591                    2                   34                  2   
4653476                    3                    9                  2   
4618280                    5                   28                  1   

         srch_children_count  srch_room_count  srch_saturday_night_bool  \
4772218                    0                1                         1   
4768857                    0                1                         0   
4681591                    2                1                         1   
4653476                    2                1                         1   
4618280                    0                1                         0   

         srch_query_affinity_score  orig_destination_distance  random_bool  
4772218                 -24.146418                1301.234406            0  
4768857                 -24.146418                  63.280000            0  
4681591                 -24.146418                 433.340000            0  
4653476                 -24.146418                 200.720000            1  
4618280                 -24.146418                1255.870000            1  

[5 rows x 62 columns]

# Export for rankLib

In [11]:
train = df[df.date_time < '2013-05-30']
train = train.sort_values(['srch_id'])
train = train.drop(['date_time', 'prop_id'], axis=1)
train['label'] = train.click_bool + 4 * train.booking_bool
train = train.drop(['click_bool', 'booking_bool'], axis=1)
to_ranklib(train,'label','srch_id',r'C:\Users\janse\OneDrive\Bureaublad\Master\Data Mining Techniques\Assignment 2\preprocessed\train.txt')
del train



['visitor_hist_starrating_mean', 'visitor_hist_starrating_std', 'visitor_hist_adr_usd_mean', 'visitor_hist_adr_usd_std', 'prop_starrating_mean', 'prop_starrating_std', 'prop_review_score_mean', 'prop_review_score_std', 'prop_brand_bool_mean', 'prop_brand_bool_std', 'prop_location_score1_mean', 'prop_location_score1_std', 'prop_location_score2_mean', 'prop_location_score2_std', 'prop_log_historical_price_mean', 'prop_log_historical_price_std', 'price_usd_mean', 'price_usd_std', 'promotion_flag_mean', 'promotion_flag_std', 'srch_length_of_stay_mean', 'srch_length_of_stay_std', 'srch_booking_window_mean', 'srch_booking_window_std', 'srch_adults_count_mean', 'srch_adults_count_std', 'srch_children_count_mean', 'srch_children_count_std', 'srch_room_count_mean', 'srch_room_count_std', 'srch_saturday_night_bool_mean', 'srch_saturday_night_bool_std', 'srch_query_affinity_score_mean', 'srch_query_affinity_score_std', 'orig_destination_distance_mean', 'orig_destination_distance_std', 'random_boo

In [ ]:
test = df[df.date_time >= '2013-05-30']
test = test.sort_values(['srch_id'])
test = test.drop(['date_time', 'prop_id'], axis=1)
test['label'] = test.click_bool + 4 * test.booking_bool
test = test.drop(['click_bool', 'booking_bool'], axis=1)
to_ranklib(test,'label','srch_id',r'C:\Users\janse\OneDrive\Bureaublad\Master\Data Mining Techniques\Assignment 2\preprocessed\test.txt')
del test

In [ ]:
testing_main = pd.read_csv(testpath, usecols=['srch_id', 'prop_id'])
df = test_eng(testing_main, train_main)
df['label'] = 0
df = df.sort_values('srch_id')
to_ranklib(df,'label','srch_id',r'C:\Users\janse\OneDrive\Bureaublad\Master\Data Mining Techniques\Assignment 2\preprocessed\kaggle_test.txt')


# Some other stuff

In [ ]:
def rate(row, mean_rate):
    if row['srch_id'] < 20:
        return mean_rate
    else:
        return row['click_bool']
    
def avg_click_rate(train_main):
    prop_click_rate = train_main[['prop_id','click_bool', 'srch_id']].groupby('prop_id').agg({'click_bool' : 'mean', 'srch_id': 'count'}).reset_index()
    mean_rate = prop_click_rate.click_bool.mean()
    prop_click_rate['click_rate'] = prop_click_rate.apply(lambda x: rate(x, mean_rate), axis=1)
    return prop_click_rate[['prop_id', 'click_rate']]

#prop_srch.sort_values(['srch_id','value'], ascending=[True, False]).head(100)
avg_rates = avg_click_rate(train_main)
print(avg_rates.head())
prop_srch = results.merge(avg_rates, on='prop_id')
prop_srch['value'] = (prop_srch['value'] + prop_srch['value'].min()) / prop_srch['value'].max()
prop_srch['click_rate'] = (prop_srch['click_rate'] - prop_srch['click_rate'].min()) / prop_srch['click_rate'].max()
prop_srch['value2'] = (prop_srch['value'] + prop_srch['click_rate']) / 2
prop_srch = prop_srch.sort_values(['srch_id', 'value2'] , ascending=[True, False])
eval_ndcg(prop_srch, 'srch_id', 'value2','actual', n=5000)

In [ ]:
train_main[train_main.prop_id == 893].price_usd.head()

In [ ]:
df = train_main[['prop_id','srch_id', 'click_bool', 'booking_bool']]
df = df.merge(avg_click_rate(train_main), on='prop_id')
df['target'] = df['click_bool'] + df['booking_bool'] * 4
eval_ndcg(df, 'srch_id','click_rate','target', n=5000)

In [15]:
# rankLib formatting:
# first value is the label (0/1/5), second value is srch_id, then there are features

with open(r'C:\Users\janse\OneDrive\Bureaublad\Master\Data Mining Techniques\Assignment 2\preprocessed\train.txt') as f:
    for i in range(20):
        print(f.readline())

0 qid:1 1:3.322413793103448 2:3.5 3:0.7259213612093934 4:182.71137931034482 5:170.74 6:94.44132932008021 7:4 8:4 9:0.0 10:4.0 11:4.0 12:0.0 13:1 14:1 15:0.0 16:2.200000000000024 17:2.2 18:0.0 19:0.025825547445255496 20:0.0149 21:0.03185471137541937 22:4.4000000000000155 23:5.03 24:1.6661063319243317 25:152.05408233276165 26:129.0 27:390.9285730663125 28:0.051457975986277875 29:0.0 30:0.22111969329662595 31:1.6569468267581475 32:1.0 33:1.1749017399520345 34:28.221269296740996 35:12.0 36:39.78547405102965 37:1.8936535162950257 38:2.0 39:0.9446962802262713 40:0.33962264150943394 41:0.0 42:0.7236252720378428 43:1.1492281303602059 44:1.0 45:0.49744562751568244 46:0.5420240137221269 47:1.0 48:0.4986587020604008 49:-20.22207173913044 50:-17.172150000000002 51:11.945580138308022 52:1760.0581861575174 53:1091.95 54:2245.9363960137625 55:0.20240137221269297 56:0.0 57:0.40213484872824407

0 qid:1 1:3.24 2:3.4400000000000004 3:0.6770632423535792 4:170.49142857142857 5:164.465 6:83.87312795545041 7